In [1]:
import pandas as pd
import numpy as np
from catboost import CatBoostRegressor
# import joblib
# import time
# from tqdm import tqdm
import warnings
warnings.filterwarnings('ignore') #warning 문구 제거
# pd.set_option('display.max_columns', None)

In [9]:
#데이터 불러오기
visit = pd.read_csv('data/visit_area_processing.csv')
travel = pd.read_csv('data/travel_result.csv')
traveler_master = pd.read_csv('data/traveler_master_result.csv')
move = pd.read_csv('data/move_result.csv')
code = pd.read_csv('data/codeB.csv')
sgg = pd.read_csv('data/sigungu_code.csv')


In [10]:
# 집, 친지집, 사무실 제거
visit_use = visit[~visit['VISIT_AREA_TYPE_CD'].isin([21,22,23])].reset_index

In [11]:
# 시군구 코드
# 'SGG_CD2'의 NaN 값을 0으로 대체한 후 int로 변환
sgg['SGG_CD2'] = sgg['SGG_CD2'].fillna(0).astype(int)

# 'SGG_CD1'와 'SGG_CD2'를 합쳐서 'TRAVEL_LIKE_SGG' 컬럼을 매핑
sgg['SGG_CODE'] = sgg['SGG_CD1'].astype(str) + sgg['SGG_CD2'].astype(str)
sgg['SGG_NAME'] = sgg['SIDO_NM'] + ' ' + sgg['SGG_NM']

# 'SGG_CD1'과 'SIDO_NM' 매핑 딕셔너리 생성
sido_mapping = dict(zip(sgg['SGG_CD1'], sgg['SIDO_NM']))

# 'SGG_CODE'와 'SGG_NAME' 매핑 딕셔너리 생성
sgg_mapping = dict(zip(sgg['SGG_CODE'], sgg['SGG_NAME']))

# SGG_CODE 목록
sgg_code_list = sgg['SGG_CODE'].astype(str).tolist()

def find_closest_sgg_code(sgg_code, sgg_code_list):
    try:
        sgg_code = int(sgg_code)
        sgg_code_list = np.array([int(code) for code in sgg_code_list])
        closest_index = (np.abs(sgg_code_list - sgg_code)).argmin()
        return str(sgg_code_list[closest_index]).zfill(5)  # 원래 형식을 맞추기 위해 5자리로 채움
    except ValueError:
        return None

# TRAVEL_LIKE_SIDO 컬럼에 매핑 적용
for i in range(1, 4):
    col_name = f'TRAVEL_LIKE_SIDO_{i}'
    traveler_master[col_name] = traveler_master[col_name].map(sido_mapping)

# TRAVEL_LIKE_SGG 컬럼에 매핑 적용 및 근처 값 대체
for i in range(1, 4):
    col_name = f'TRAVEL_LIKE_SGG_{i}'
    for index, value in traveler_master[col_name].astype(str).items():
        if value in sgg_mapping:
            traveler_master.at[index, col_name] = sgg_mapping[value]
        else:
            closest_code = find_closest_sgg_code(value, sgg_code_list)
            if closest_code:
                traveler_master.at[index, col_name] = sgg_mapping.get(closest_code, 'Unknown')
            else:
                traveler_master.at[index, col_name] = 'Unknown'

# 주소가 3단어인 경우를 처리
def convert_to_two_words(address):
    words = address.split()
    if len(words) == 3:
        return ' '.join(words[:2])
    return address

# 주소 변환 적용
traveler_master['TRAVEL_LIKE_SGG_1'] = traveler_master['TRAVEL_LIKE_SGG_1'].apply(convert_to_two_words)

# # (매핑용 코드)
# code_tsy = code[code['cd_a'] == 'TSY'][['cd_b','cd_nm']]
# code_tsy['cd_b'] = code_tsy['cd_b'].astype(int)
# code_tsy = dict(zip(code_tsy['cd_b'], code_tsy['cd_nm']))

# # # 여행스타일 매핑
# traveler_master['STYL1'] = traveler_master['TRAVEL_STYL_1'].map(code_tsy)
# traveler_master['STYL2'] = traveler_master['TRAVEL_STYL_1'].map(code_tsy)
# traveler_master['STYL3'] = traveler_master['TRAVEL_STYL_1'].map(code_tsy)
# traveler_master['STYL4'] = traveler_master['TRAVEL_STYL_1'].map(code_tsy)
# traveler_master['STYL5'] = traveler_master['TRAVEL_STYL_1'].map(code_tsy)
# traveler_master['STYL6'] = traveler_master['TRAVEL_STYL_1'].map(code_tsy)
# traveler_master['STYL7'] = traveler_master['TRAVEL_STYL_1'].map(code_tsy)
# traveler_master['STYL8'] = traveler_master['TRAVEL_STYL_1'].map(code_tsy)
# traveler_master['STYL9'] = traveler_master['TRAVEL_STYL_1'].map(code_tsy)

# 여행master, 여행 merge
merge_trav = pd.merge(traveler_master, travel, on = 'TRAVELER_ID')

In [ ]:
# 방문지 정보 추가 매핑
# use_data = pd.merge(merge_trav, visit, on = 'TRAVEL_ID')

In [98]:
## 여행지 추가를 위한 추가 데이터

# 방문지 정보 여행지 정리
id_check = travel[['TRAVEL_ID','TRAVELER_ID']]
id_check = id_check.drop_duplicates().reset_index(drop=True)

# 방문지 정보 데이터 처리
visit_use = visit.dropna(subset=['ROAD_NM_ADDR'])
visit_use = visit_use.reset_index(drop = True)

# 시도/군구 변수 생성
visit_use['sido'] = visit_use['ROAD_NM_ADDR'].apply(lambda x: x.split(' ')[0] if isinstance(x, str) and len(x.split(' ')) > 1 else np.nan)
visit_use['gungu'] = visit_use['ROAD_NM_ADDR'].apply(lambda x: x.split(' ')[1] if isinstance(x, str) and len(x.split(' ')) > 1 else np.nan)

list(visit_use['sido'].unique())
sgg['SIDO_NM'].unique()
sgg_list = list(sgg['SGG_NM'].dropna().unique())
sido_all = list(sgg['SIDO_NM'].unique())

# 각 시군구 데이터에서 앞 단어만 추출
sgg_all = [location.split()[0] for location in sgg_list]

visit_use = visit_use[visit_use['sido'].isin(sido_all)]
visit_use = visit_use[visit_use['gungu'].isin(sgg_all)]
visit_use = visit_use.dropna(subset=['sido']).reset_index(drop=True)
visit_use = visit_use.dropna(subset=['gungu']).reset_index(drop=True)

# mapping = {
#     '서울': '서울특별시',
#     '부산': '부산광역시',
#     '대구': '대구광역시',
#     '인천': '인천광역시',
#     '광주': '광주광역시',
#     '대전': '대전광역시',
#     '울산': '울산광역시',
#     '세종': '세종특별자치시',
#     '경기': '경기도',
#     '강원': '강원도',
#     '충북': '충청북도',
#     '충남': '충청남도',
#     '전북': '전라북도',
#     '전남': '전라남도',
#     '경북': '경상북도',
#     '경남': '경상남도',
#     '제주': '제주특별자치도',
# }

# visit_use['sido'] = visit_use['sido'].map(mapping)

visit_use['LOCATION'] = visit_use['sido'] + ' ' + visit_use['gungu']

use_data = pd.merge(merge_trav, visit_use, on = 'TRAVEL_ID')

In [99]:
use_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 54983 entries, 0 to 54982
Data columns (total 47 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   TRAVELER_ID                54983 non-null  object 
 1   GENDER                     54983 non-null  object 
 2   AGE_GRP                    54983 non-null  int64  
 3   TRAVEL_LIKE_SIDO_1         54983 non-null  object 
 4   TRAVEL_LIKE_SGG_1          54983 non-null  object 
 5   TRAVEL_LIKE_SIDO_2         54983 non-null  object 
 6   TRAVEL_LIKE_SGG_2          54983 non-null  object 
 7   TRAVEL_LIKE_SIDO_3         54983 non-null  object 
 8   TRAVEL_LIKE_SGG_3          54983 non-null  object 
 9   TRAVEL_STYL_1              54983 non-null  int64  
 10  TRAVEL_STYL_2              54983 non-null  int64  
 11  TRAVEL_STYL_3              54983 non-null  int64  
 12  TRAVEL_STYL_4              54983 non-null  int64  
 13  TRAVEL_STYL_5              54983 non-null  int

In [100]:
use_data['TRAVEL_STATUS_DESTINATION'].unique()

array(['서울', '경기', '인천', '강원', '도서 지역', '경남', '전북', '대전', '부산', '경북',
       '대구', '울산', '충북', '전남', '충남', '광주', '세종', '제주'], dtype=object)

In [ ]:
# 1. 여행 장소(시도) 추천 시스템

from catboost import CatBoostClassifier, Pool
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

# 범주형 변수를 숫자로 인코딩
label_encoders = {
    'GENDER': LabelEncoder(),
    'TRAVEL_STATUS_RESIDENCE': LabelEncoder(),
}

for col, encoder in label_encoders.items():
    use_data[col] = encoder.fit_transform(use_data[col])

# 입력 데이터와 출력 데이터
X = use_data[['AGE_GRP', 'GENDER', 'TRAVEL_STATUS_RESIDENCE', 'TRAVEL_STYL_1', 'TRAVEL_STYL_2',
              'TRAVEL_STYL_3', 'TRAVEL_STYL_4', 'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8']]
y = use_data['TRAVEL_LIKE_SGG_1']

# # 빈도수 계산 및 가중치 설정
# class_counts = y.value_counts()
# class_weights = {cls: 1.0 / count for cls, count in class_counts.items()}
# use_data['weight'] = use_data['TRAVEL_LIKE_SGG_1'].map(class_weights)


# 데이터 분할
X_train, X_test, y_train, y_test, = train_test_split(X, y, test_size=0.2, random_state=42)


# from imblearn.over_sampling import RandomOverSampler

# rds = RandomOverSampler(random_state=42)
# X_train_resample, y_train_resample = rds.fit_resample(X_train,y_train)
# print(f'shape : {X_train.shape}, {X_train_resample.shape}')

In [102]:

# Destination 예측 모델
model = CatBoostClassifier(iterations=100, learning_rate=0.1, depth=7, verbose=10)
model.fit(X_train, y_train)

# Destination 예측
y_pred = model.predict(X_test)

# 평가 지표 계산
accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred, average='weighted')
recall = recall_score(y_test, y_pred, average='weighted')
f1 = f1_score(y_test, y_pred, average='weighted')

# 결과 출력
print("Destination 모델 성능:")
print(f"Accuracy: {accuracy:.4f}")
print(f"Precision: {precision:.4f}")
print(f"Recall: {recall:.4f}")
print(f"F1 Score: {f1:.4f}")
print()


0:	learn: 5.2062372	total: 1.48s	remaining: 2m 26s
10:	learn: 4.2717541	total: 14.5s	remaining: 1m 57s
20:	learn: 3.8455925	total: 24s	remaining: 1m 30s
30:	learn: 3.5561268	total: 36.2s	remaining: 1m 20s
40:	learn: 3.2464019	total: 46.9s	remaining: 1m 7s
50:	learn: 3.0109894	total: 54.4s	remaining: 52.3s
60:	learn: 2.7984549	total: 1m 1s	remaining: 39.5s
70:	learn: 2.5994692	total: 1m 12s	remaining: 29.5s
80:	learn: 2.4632928	total: 1m 20s	remaining: 18.9s
90:	learn: 2.3289789	total: 1m 29s	remaining: 8.89s
99:	learn: 2.2087897	total: 1m 41s	remaining: 0us
Destination 모델 성능:
Accuracy: 0.4970
Precision: 0.5428
Recall: 0.4970
F1 Score: 0.4873



In [ ]:
## 장소 추천 시스템
selected_columns = [
    'AGE_GRP', 'GENDER', 'TRAVEL_STATUS_RESIDENCE',
    'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
    'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
    'LOCATION', 'VISIT_AREA_NM'
]
final_data = use_data[selected_columns]

from sklearn.preprocessing import LabelEncoder


# # 학습 데이터에서 드물게 등장하는 여행지를 "기타"로 처리
# threshold = 10  # 임계값 설정 (예: 50회 미만 방문)
# visit_counts = final_data['VISIT_AREA_NM'].value_counts()
# final_data['VISIT_AREA_NM'] = final_data['VISIT_AREA_NM'].apply(
#     lambda x: x if visit_counts[x] >= threshold else '기타'
# )

# 범주형 데이터 인코딩
categorical_cols = ['AGE_GRP', 'GENDER', 'TRAVEL_STATUS_RESIDENCE', 'LOCATION']
label_encoders = {}

for col in categorical_cols:
    le = LabelEncoder()
    final_data[col] = le.fit_transform(final_data[col])
    label_encoders[col] = le  # 나중에 역변환을 위해 저장


# 타겟 변수와 입력 변수 분리
X_place = final_data.drop(columns=['VISIT_AREA_NM'])
y_place = final_data['VISIT_AREA_NM']

from sklearn.model_selection import train_test_split

# 데이터 분할
X_place_train, X_place_test, y_place_train, y_place_test = train_test_split(X_place, y_place, test_size=0.2, random_state=50)

# 라벨 인코더 생성 및 학습 데이터로 피팅
label_encoder = LabelEncoder()
y_train_encoded = label_encoder.fit_transform(y_place_train)

# 테스트 데이터도 동일한 인코더로 변환
y_test_encoded = label_encoder.transform(y_place_test)

# 클래스 수 확인
num_classes = len(label_encoder.classes_)
print("Number of classes:", num_classes)

Number of classes: 729


In [105]:
import numpy as np

# 라벨 값 범위 검증
assert np.all((y_train_encoded >= 0) & (y_train_encoded < num_classes)), "Train labels are out of range!"
assert np.all((y_test_encoded >= 0) & (y_test_encoded < num_classes)), "Test labels are out of range!"

In [ ]:
from sklearn.model_selection import train_test_split
import lightgbm as lgb

# 데이터 로드 및 전처리
# final_data = pd.read_csv('final_data.csv')  # 예시 데이터
X = final_data.drop(columns=['VISIT_AREA_NM'])
y = final_data['VISIT_AREA_NM']

# TRAVEL_STATUS_DESTINATION별로 데이터 분리
destination_models = {}
for destination in final_data['TRAVEL_STATUS_DESTINATION'].unique():
    # 특정 TRAVEL_STATUS_DESTINATION에 해당하는 데이터만 선택
    subset = final_data[final_data['LOCATION'] == destination]
    X_subset = subset.drop(columns=['VISIT_AREA_NM', 'LOCATION'])
    y_subset = subset['VISIT_AREA_NM']
    
    # 데이터 분할
    X_train, X_test, y_train, y_test = train_test_split(X_subset, y_subset, test_size=0.2, random_state=42)
    
    # 라벨 인코딩
    label_encoder = LabelEncoder()
    y_train_encoded = label_encoder.fit_transform(y_train)
    y_test_encoded = label_encoder.transform(y_test)
    
    # LightGBM 데이터셋 생성
    train_data = lgb.Dataset(X_train, label=y_train_encoded)
    test_data = lgb.Dataset(X_test, label=y_test_encoded, reference=train_data)
    
    # LightGBM 파라미터 설정
    params = {
        'objective': 'multiclass',
        'num_class': len(label_encoder.classes_),
        'metric': 'multi_logloss',
        'boosting_type': 'gbdt',
        'random_state': 42
    }
    
    # 모델 학습
    model = lgb.train(params, train_data, valid_sets=[test_data], num_boost_round=100, early_stopping_rounds=10)
    
    # 모델 저장
    destination_models[destination] = (model, label_encoder)

# 새로운 여행자 데이터 예측
new_traveler = pd.DataFrame({
    'AGE_GRP': [3],
    'GENDER': [1],
    'TRAVEL_STATUS_RESIDENCE': [5],
    'TRAVEL_STYL_1': [5],
    'TRAVEL_STYL_2': [4],
    'TRAVEL_STYL_3': [3],
    'TRAVEL_STYL_4': [2],
    'TRAVEL_STYL_5': [1],
    'TRAVEL_STYL_6': [4],
    'TRAVEL_STYL_7': [5],
    'TRAVEL_STYL_8': [3],
    'TRAVEL_STATUS_DESTINATION': [7]  # 예: 제주도
})

# TRAVEL_STATUS_DESTINATION 값 확인
destination = new_traveler['TRAVEL_STATUS_DESTINATION'].iloc[0]

# 해당 목적지에 맞는 모델 선택
if destination in destination_models:
    model, label_encoder = destination_models[destination]
    predicted_probs = model.predict(new_traveler.drop(columns=['TRAVEL_STATUS_DESTINATION']))
    top_10_indices = predicted_probs.argsort(axis=1)[:, -10:]
    recommended_areas = [label_encoder.inverse_transform([idx])[0] for idx in top_10_indices[0]]
    print("Recommended Travel Destinations:", recommended_areas)
else:
    print("No model available for the given destination.")

In [106]:
import lightgbm as lgb
from sklearn.metrics import classification_report

# LightGBM 데이터셋 생성
train_data = lgb.Dataset(X_place_train, label=y_train_encoded)
test_data = lgb.Dataset(X_place_test, label=y_test_encoded, reference=train_data)

# 모델 학습
params = {
    'objective': 'multiclass',
    'num_class': num_classes,  # 클래스 수 설정
    'metric': 'multi_logloss',
    'boosting_type': 'gbdt',
    'random_state': 42
}
model = lgb.train(params, train_data, valid_sets=[test_data], num_boost_round=100)

# 예측
y_pred = model.predict(X_place_test, num_iteration=model.best_iteration)
y_pred_classes = y_pred.argmax(axis=1)

# 성능 평가
print(classification_report(y_test_encoded, y_pred_classes))

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002375 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 315
[LightGBM] [Info] Number of data points in the train set: 43986, number of used features: 12
[LightGBM] [Info] Start training from score -8.612185
[LightGBM] [Info] Start training from score -8.389042
[LightGBM] [Info] Start training from score -8.293731
[LightGBM] [Info] Start training from score -7.136279
[LightGBM] [Info] Start training from score -7.556132
[LightGBM] [Info] Start training from score -8.126677
[LightGBM] [Info] Start training from score -7.556132
[LightGBM] [Info] Start training from score -7.472751
[LightGBM] [Info] Start training from score -8.745717
[LightGBM] [Info] Start training from score -8.293731
[LightGBM] [Info] Start training from score -7.513573
[LightGBM] [Info] Start training from score -7.983576
[LightGBM] [Info] Start training from score -7.695894
[LightGBM]

In [112]:
# 새로운 여행자 데이터 예시
new_traveler = pd.DataFrame({
    'AGE_GRP': [3],  # 예: 30대
    'GENDER': [1],   # 예: 남성
    'TRAVEL_STATUS_RESIDENCE': [3],  # 예: 서울
    'TRAVEL_STYL_1': [5],
    'TRAVEL_STYL_2': [4],
    'TRAVEL_STYL_3': [3],
    'TRAVEL_STYL_4': [2],
    'TRAVEL_STYL_5': [7],
    'TRAVEL_STYL_6': [4],
    'TRAVEL_STYL_7': [5],
    'TRAVEL_STYL_8': [3],
    'LOCATION': [33]  # 예: 제주도
})

# 예측 확률 계산
predicted_probs = model.predict(new_traveler[X_place_train.columns], num_iteration=model.best_iteration)

# 결과 확인
print("Predicted probabilities shape:", predicted_probs.shape)

# 상위 10개 여행지 추천
top_10_indices = predicted_probs.argsort(axis=1)[:,:]
recommended_areas = [label_encoder.inverse_transform([idx])[0] for idx in top_10_indices[0]]
destination = label_encoders['LOCATION'].inverse_transform(new_traveler['LOCATION'])

# 결과 출력
print("LOCATION: ", destination)
print("Recommended Travel Destinations:", recommended_areas)

Predicted probabilities shape: (1, 729)
LOCATION:  ['경기도 안성시']
Recommended Travel Destinations: ['1913 송정역시장', '외암민속마을', '외옹치 바다 향기로', '외할머니 솜씨', '용두산공원', '용머리해안', '용연계곡', '용연구름다리', '우도', '외돌개 전망대', '우도봉 입구', '우유 창고', '운대리 자작나무 숲', '웅진백제역사관', '웅천친수공원', '원조태평소국밥', '월령선인장군락지', '월미테마파크', '월영교', '우수영 국민관광지', '외돌개', '외도보타니아', '외도널서리', '예당호 출렁다리', '예산 상설시장', '예술의전당', '옛 군산세관', '오동도', '오동동 김밥', '오목대', '오브레멘', '오션솔레뷰호텔', '오씨칼국수', '오씨칼국수 도룡점', '오이도 빨강등대', '오저여', '오죽헌', '옥천 전통문화체험관', '올라 카이 송도파크호텔', '올레길 10코스(화순-모슬포 올레)', '올림픽공원', '와인터널', '월정교', '월정리해수욕장', '유달 콩물 본점', '유성온천공원 족욕체험장', '인사동 문화의 거리', '인천 차이나타운', '일산 호수공원', '일월 수목원', '임진각 평화누리', '자갈치시장', '자라섬', '자만 벽화마을', '자매 갈비전골', '자유 공원', '잠실종합운동장 올림픽 주경기장', '장도', '장생포 고래 박물관', '장생포 고래문화마을', '장안문', '장원 막국수', '장태산자연휴양림', '장항 스카이워크', '장화리 일몰조망지', '인더웅', '예당호 모노레일', '이호테우해수욕장', '이터널저니', '유성호텔', '유스퀘어 광주종합버스터미널', '유월드 루지 테마파크', '유탑 마리나호텔 리조트', '육거리종합시장', '으능정이 문화의 거리', '으능정이 스카이로드', '은파호수공원', '을왕리해수욕장', '의림지', '이가리 닻 전망대', '이순신 수제버거', '이순신공원', '이순신광장

In [113]:
# TRAVEL_STATUS_DESTINATION에 맞는 여행지 필터링
destination = new_traveler['LOCATION'].iloc[0]
filtered_areas = []
for idx in top_10_indices[0]:
    area = label_encoder.inverse_transform([idx])[0]
    if area.startswith(str(destination)):  # 또는 다른 조건 추가
        filtered_areas.append(area)

print("Filtered Recommended Travel Destinations:", filtered_areas)

Filtered Recommended Travel Destinations: []


In [ ]:
# 새로운 데이터 생성 함수
def generate_random_data(n_samples):
    np.random.seed(43)  # 랜덤 시드 설정

    genders = np.random.choice(['남', '여'], size=n_samples) 
    ages = np.random.choice([20, 30, 40, 50, 60], size=n_samples)  
    residences = np.random.choice(sido_all, size=n_samples)
    travel_styles = {
        'TRAVEL_STYL_1': np.random.choice([1,2,3,4,5,6,7], size=n_samples),
        'TRAVEL_STYL_2': np.random.choice([1,2,3,4,5,6,7], size=n_samples),
        'TRAVEL_STYL_3': np.random.choice([1,2,3,4,5,6,7], size=n_samples),
        'TRAVEL_STYL_4': np.random.choice([1,2,3,4,5,6,7], size=n_samples),
        'TRAVEL_STYL_5': np.random.choice([1,2,3,4,5,6,7], size=n_samples),
        'TRAVEL_STYL_6': np.random.choice([1,2,3,4,5,6,7], size=n_samples),
        'TRAVEL_STYL_7': np.random.choice([1,2,3,4,5,6,7], size=n_samples),
        'TRAVEL_STYL_8': np.random.choice([1,2,3,4,5,6,7], size=n_samples),
    }

    data = {
        'GENDER': genders,
        'AGE_GRP': ages,
        'TRAVEL_STATUS_RESIDENCE': residences,
        'TRAVEL_STYL_1': travel_styles['TRAVEL_STYL_1'],
        'TRAVEL_STYL_2': travel_styles['TRAVEL_STYL_2'],
        'TRAVEL_STYL_3': travel_styles['TRAVEL_STYL_3'],
        'TRAVEL_STYL_4': travel_styles['TRAVEL_STYL_4'],
        'TRAVEL_STYL_5': travel_styles['TRAVEL_STYL_5'],
        'TRAVEL_STYL_6': travel_styles['TRAVEL_STYL_6'],
        'TRAVEL_STYL_7': travel_styles['TRAVEL_STYL_7'],
        'TRAVEL_STYL_8': travel_styles['TRAVEL_STYL_8'],
    }


    new_df = pd.DataFrame(data)
    return new_df

# 새로운 데이터 생성 (예시: 5개의 샘플 생성)
n_samples = 10
random_data = generate_random_data(n_samples)

for col, encoder in label_encoders.items():
    if col in random_data.columns:
        random_data[col] = encoder.transform(random_data[col])

# 새로운 데이터 예측
predicted_destinations = model.predict(random_data)
predicted_destinations_label = label_encoders['TRAVEL_LIKE_SGG_1'].inverse_transform(predicted_destinations)

# 명소 추천 함수 정의
def recommend_attractions(destination, visit_data, top_n=10):
    attractions = visit_data[visit_data['LOCATION'] == destination]
    attraction_counts = attractions['VISIT_AREA_NM'].value_counts().head(top_n)
    top_attractions = attractions[attractions['VISIT_AREA_NM'].isin(attraction_counts.index)]
    return top_attractions.drop_duplicates(subset=['VISIT_AREA_NM'])


# 추천된 여행지와 명소 출력 및 결과 저장
results = []
for i, destination in enumerate(predicted_destinations_label):
    attractions = recommend_attractions(destination, visit_use)
    attractions_names = ', '.join(attractions['VISIT_AREA_NM'].tolist())
    df_gender = label_encoders['GENDER'].inverse_transform([random_data.iloc[i]['GENDER']])[0]
    df_age = random_data.iloc[i]['AGE_GRP']
    df_residence = label_encoders['TRAVEL_STATUS_RESIDENCE'].inverse_transform([random_data.iloc[i]['TRAVEL_STATUS_RESIDENCE']])[0]
    df_STYL = label_encoders['STYL1'].inverse_transform([random_data.iloc[i]['STYL1']])[0]
    print(f"GENDER: {df_gender}, AGE: {df_age}, RESIDENCE: {df_residence}, TRAVEL STYLE: {df_STYL}")
    print(f"추천 여행지: {destination}")
    print(f"추천 명소: {attractions_names}")
    print('==='*10)
    for index,row in attractions.iterrows():
        results.append({
            'GENDER': df_gender,            
            'AGE_GRP': df_age,
            'TRAVEL_STATUS_RESIDENCE': df_residence,
            'STYL1': df_STYL,
            'Predicted_Destination': destination,
            'Recommended_Places': row['VISIT_AREA_NM'],
            'Recommended_Address' : row['ROAD_NM_ADDR'],
            'X_COORD' : row['X_COORD'],
            'Y_COORD' : row['Y_COORD']
    })

# 결과를 데이터프레임으로 변환
results_df = pd.DataFrame(results)

GENDER: 남, AGE: 50, RESIDENCE: 충청남도, TRAVEL STYLE: 도시 선호 약간선호
추천 여행지: 대전광역시 유성구
추천 명소: 국립 중앙과학관, 엑스포과학공원 한빛탑, 롯데시티 호텔 대전, 대전 신세계 아트앤사이언스, 오씨칼국수 도룡점, 성심당 DCC점, 대전 어린이 회관, 원조태평소국밥, 유성온천공원 족욕체험장, 유성호텔
GENDER: 남, AGE: 40, RESIDENCE: 대구광역시, TRAVEL STYLE: 자연 선호 약간선호
추천 여행지: 경상북도 영덕군
추천 명소: 고래불해수욕장, 스포트리조트, 영덕해맞이공원, 삼사해상공원, 벌열 메타세쿼이아 숲, 장사상륙작전 전승기념관, 대게 궁, 장사해수욕장, 영덕 해 파랑공원, 그리가다
GENDER: 여, AGE: 20, RESIDENCE: 인천광역시, TRAVEL STYLE: 자연 선호 중간선호
추천 여행지: 인천광역시 남동구
추천 명소: 통 큰 해물 손칼국수 소래포구 본점, 소래포구, 소래포구 종합어시장, 파크 마린 호텔, 인천대공원, 라마다 인천 호텔, 소래습지생태공원, 메가박스 인천 논현, 그랜드 팰리스 호텔 인천, 남동공단 떡볶이
GENDER: 여, AGE: 50, RESIDENCE: 광주광역시, TRAVEL STYLE: 자연 선호 매우선호
추천 여행지: 전라남도 영광군
추천 명소: 불갑사, 백수해안도로, 영광 칠산 다워, 야월 교회, 카페 보리, 국제식당, 백제불교 최초 도래지 부용리, 영광 물 무산 행복 숲 질퍽질퍽 맨발 황톳길, 민속적, 법성 토우
GENDER: 여, AGE: 40, RESIDENCE: 광주광역시, TRAVEL STYLE: 자연 선호 약간선호
추천 여행지: 전라남도 완도군
추천 명소: 방파제, 범바위, 완도타워, 신지명사십리해수욕장, 서편제촬영지, 완도네시아, 지리해수욕장, 카페마르, 신흥해수욕장, 청산도게스트하우스
GENDER: 남, AGE: 50, RESIDENCE: 제주특별자치도, TRAVEL STYLE: 도시 선호 약간선호
추천 여행지: 대전광역

In [19]:
results_df.head()

GENDER  AGE_GRP TRAVEL_STATUS_RESIDENCE       STYL1 Predicted_Destination  \
0      남       50                    충청남도  도시 선호 약간선호             대전광역시 유성구   
1      남       50                    충청남도  도시 선호 약간선호             대전광역시 유성구   
2      남       50                    충청남도  도시 선호 약간선호             대전광역시 유성구   
3      남       50                    충청남도  도시 선호 약간선호             대전광역시 유성구   
4      남       50                    충청남도  도시 선호 약간선호             대전광역시 유성구   

  Recommended_Places     Recommended_Address     X_COORD    Y_COORD  
0           국립 중앙과학관      대전광역시 유성구 대덕대로 481  127.375212  36.376069  
1        엑스포과학공원 한빛탑      대전광역시 유성구 대덕대로 480  127.388084  36.376629  
2         롯데시티 호텔 대전  대전광역시 유성구 엑스포로123번길 33  127.393034  36.376192  
3     대전 신세계 아트앤사이언스        대전광역시 유성구 엑스포로 1  127.381377  36.375242  
4          오씨칼국수 도룡점  대전광역시 유성구 엑스포로151번길 19  127.394782  36.376333